# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening an **Indian restaurant** in **New York city**, United States of America.

Since there are lots of restaurants in New York we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no Indian restaurants in vicinity**. 

We will use data science techniques to come up with a list of most ideal neighborhoods based on this criteria so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:

* number of existing restaurants in the neighborhood (any type of restaurant)
* number of indian restaurants in the neighborhood, if any

Following data sources will be needed to extract/generate the required information:

* Geospatial data to get the latitude and longitude of each neighbourhood :  https://geo.nyu.edu/download/file/nyu-2451-34572-geojson.json
* Data on venue details like Restaurants, Stores e.t.c in the neighborhoods : FourSquare API

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.1.1c             |       h516909a_0         2.1 MB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    certifi-2019.9.11          |           py36_0         147 KB  conda-forge
    ca-certificates-2019.9.11  |       hecc5488_0         144 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

## 1. Download and Explore Dataset

In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


#### Load and explore the data

Next, let's load the data.

In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Let's take a quick look at the data.

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

Notice how all the relevant data is in the *features* key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.

In [5]:
neighborhoods_data = newyork_data['features']

Let's take a look at the first item in this list.

In [6]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Tranform the data into a *pandas* dataframe

The next task is essentially transforming this data of nested Python dictionaries into a *pandas* dataframe. So let's start by creating an empty dataframe.

In [7]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Take a look at the empty dataframe to confirm that the columns are as intended.

In [8]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Then let's loop through the data and fill the dataframe one row at a time.

In [9]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Quickly examine the resulting dataframe.

In [10]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

And make sure that the dataset has all 5 boroughs and 306 neighborhoods.

In [11]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


#### Use geopy library to get the latitude and longitude values of New York City.

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>ny_explorer</em>, as shown below.

In [12]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### Create a map of New York with neighborhoods superimposed on top.

In [13]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [14]:
CLIENT_ID = 'KMQP3YJJ3Q35BMMX0TVQUUFUMZE2JOWLI5GYNK2TSU0AMFCC' # your Foursquare ID
CLIENT_SECRET = 'D0545BSEWF4PVUKT2RRQ3PQDRLLMINDRMVFCHH2M2U0A2GFR' # your Foursquare Secret
VERSION = '20191210' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: KMQP3YJJ3Q35BMMX0TVQUUFUMZE2JOWLI5GYNK2TSU0AMFCC
CLIENT_SECRET:D0545BSEWF4PVUKT2RRQ3PQDRLLMINDRMVFCHH2M2U0A2GFR


#### Let's explore the first neighborhood in our dataframe.

Get the neighborhood's name.

In [15]:
neighborhoods.loc[0, 'Neighborhood']

'Wakefield'

#### Now, let's get the top 100 venues that are in New York city within a radius of 5000 meters.

First, let's create the GET request URL. Name your URL **url**.

In [17]:
LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 5000 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
    longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=KMQP3YJJ3Q35BMMX0TVQUUFUMZE2JOWLI5GYNK2TSU0AMFCC&client_secret=D0545BSEWF4PVUKT2RRQ3PQDRLLMINDRMVFCHH2M2U0A2GFR&v=20191210&ll=40.7127281,-74.0060152&radius=5000&limit=100'

Send the GET request and examine the resutls

In [18]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5da2417f396de0002c5b6986'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': '$-$$$$', 'key': 'price'}]},
  'headerLocation': 'New York',
  'headerFullLocation': 'New York',
  'headerLocationGranularity': 'city',
  'totalResults': 233,
  'suggestedBounds': {'ne': {'lat': 40.757728145000044,
    'lng': -73.94675840634194},
   'sw': {'lat': 40.667728054999955, 'lng': -74.06527199365804}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '57f0689d498e7d49d9189369',
       'name': 'The Bar Room at Temple Court',
       'location': {'address': '123 Nassau St',
        'lat': 40.7114477287544,
        'lng': -74.00680157032005,
        'labeledLatLngs': [{'label':

In [19]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [20]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name              categories        lat  \
0          The Bar Room at Temple Court               Hotel Bar  40.711448   
1  Four Seasons Hotel New York Downtown                   Hotel  40.712612   
2                                 Korin  Furniture / Home Store  40.714824   
3                    Aire Ancient Baths                     Spa  40.718141   
4              9/11 Memorial North Pool           Memorial Site  40.712077   

         lng  
0 -74.006802  
1 -74.009380  
2 -74.009404  
3 -74.004941  
4 -74.013187

In [21]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


## 2. Explore Neighborhoods in New York city

#### Let's create a function to repeat the same process to all the neighborhoods in New York City

In [22]:
def getNearbyVenues(names, latitudes, longitudes, radius=5000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *newyork_venues*.

In [23]:
newyork_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

#### Let's check the size of the resulting dataframe

In [24]:
print(newyork_venues.shape)
newyork_venues.head()

(30549, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                      Venue  Venue Latitude  Venue Longitude  \
0          Lollipops Gelato       40.894123       -73.845892   
1        Ripe Kitchen & Bar       40.898152       -73.838875   
2           Ali's Roti Shop       40.894036       -73.856935   
3  Kingston Tropical Bakery       40.888568       -73.859885   
4                   Jimbo's       40.891740       -73.858226   

         Venue Category  
0          Dessert Shop  
1  Caribbean Restaurant  
2  Caribbean Restaurant  
3                Bakery  
4          Burger Joint

Let's check how many venues were returned for each neighborhood

In [25]:
newyork_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                     100                     100   
Annadale                                     100                     100   
Arden Heights                                100                     100   
Arlington                                    100                     100   
Arrochar                                     100                     100   
Arverne                                       94                      94   
Astoria                                      100                     100   
Astoria Heights                              100                     100   
Auburndale                                   100                     100   
Bath Beach                                   100                     100   
Battery Park City                            100                     100   
Bay Ridge                                    100                     100   
Bay Terrace                                  200                     200   
Baychester                                   100                     100   
Bayside                                      100                     100   
Bayswater                                    100                     100   
Bedford Park                                 100                     100   
Bedford Stuyvesant                           100                     100   
Beechhurst                                   100                     100   
Bellaire                                     100                     100   
Belle Harbor                                 100                     100   
Bellerose                                    100                     100   
Belmont                                      100                     100   
Bensonhurst                                  100                     100   
Bergen Beach                                 100                     100   
Blissville                                   100                     100   
Bloomfield                                   100                     100   
Boerum Hill                                  100                     100   
Borough Park                                 100                     100   
Breezy Point                                 100                     100   
Briarwood                                    100                     100   
Brighton Beach                               100                     100   
Broad Channel                                 99                      99   
Broadway Junction                            100                     100   
Bronxdale                                    100                     100   
Brooklyn Heights                             100                     100   
Brookville                                   100                     100   
Brownsville                                  100                     100   
Bulls Head                                   100                     100   
Bushwick                                     100                     100   
Butler Manor                                 100                     100   
Cambria Heights                              100                     100   
Canarsie                                     100                     100   
Carnegie Hill                                100                     100   
Carroll Gardens                              100                     100   
Castle Hill                                  100                     100   
Castleton Corners                            100                     100   
Central Harlem                               100                     100   
Charleston                                   100                     100   
Chelsea                                      200                     200   
Chinatown                                    100                     100   

#### Let's find out how many unique categories can be curated from all the returned venues

In [26]:
print('There are {} uniques categories.'.format(len(newyork_venues['Venue Category'].unique())))

There are 347 uniques categories.


## 3. Analyze Each Neighborhood

In [27]:
# one hot encoding
newyork_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
newyork_onehot['Neighborhood'] = newyork_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [newyork_onehot.columns[-1]] + list(newyork_onehot.columns[:-1])
newyork_onehot = newyork_onehot[fixed_columns]

newyork_onehot.head()

Zoo Exhibit  Accessories Store  African Restaurant  Airport Food Court  \
0            0                  0                   0                   0   
1            0                  0                   0                   0   
2            0                  0                   0                   0   
3            0                  0                   0                   0   
4            0                  0                   0                   0   

   Airport Lounge  Airport Service  American Restaurant  Animal Shelter  \
0               0                0                    0               0   
1               0                0                    0               0   
2               0                0                    0               0   
3               0                0                    0               0   
4               0                0                    0               0   

   Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0         0       0                 0                       0            0   
1         0       0                 0                       0            0   
2         0       0                 0                       0            0   
3         0       0                 0                       0            0   
4         0       0                 0                       0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Austrian Restaurant  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                    0          0           0       0     0    0   
1                    0          0           0       0     0    0   
2                    0          0           0       0     0    0   
3                    0          0           0       1     0    0   
4                    0          0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Beach  Beach Bar  \
0               0                 0                 0      0          0   
1               0                 0                 0      0          0   
2               0                 0                 0      0          0   
3               0                 0                 0      0          0   
4               0                 0                 0      0          0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Shop  Bike Trail  \
0         0            0           0              0          0           0   
1         0            0           0              0          0           0   
2         0            0           0              0          0           0   
3         0            0           0              0          0           0   
4         0            0           0              0          0           0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Botanical Garden  Boutique  \
0       0           0              0          0                 0         0   
1       0           0              0          0                 0         0   
2       0           0              0          0                 0         0   
3       0           0              0          0                 0         0   
4       0           0              0          0                 0         0   

   Bowling Alley  Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0           0                     0               0        0   
1              0           0                     0               0        0   
2              0           0                     0               0        0   
3              0           0               

And let's examine the new dataframe size.

In [28]:
newyork_onehot.shape

(30549, 347)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [29]:
newyork_grouped = newyork_onehot.groupby('Neighborhood').mean().reset_index()
newyork_grouped

Neighborhood  Zoo Exhibit  Accessories Store  \
0                     Allerton         0.03           0.000000   
1                     Annadale         0.00           0.000000   
2                Arden Heights         0.00           0.000000   
3                    Arlington         0.00           0.020000   
4                     Arrochar         0.00           0.000000   
5                      Arverne         0.00           0.000000   
6                      Astoria         0.00           0.000000   
7              Astoria Heights         0.00           0.000000   
8                   Auburndale         0.00           0.000000   
9                   Bath Beach         0.00           0.000000   
10           Battery Park City         0.00           0.000000   
11                   Bay Ridge         0.00           0.000000   
12                 Bay Terrace         0.00           0.000000   
13                  Baychester         0.01           0.000000   
14                     Bayside         0.00           0.000000   
15                   Bayswater         0.00           0.000000   
16                Bedford Park         0.02           0.000000   
17          Bedford Stuyvesant         0.00           0.000000   
18                  Beechhurst         0.00           0.000000   
19                    Bellaire         0.00           0.000000   
20                Belle Harbor         0.00           0.000000   
21                   Bellerose         0.00           0.000000   
22                     Belmont         0.03           0.000000   
23                 Bensonhurst         0.00           0.000000   
24                Bergen Beach         0.00           0.000000   
25                  Blissville         0.00           0.000000   
26                  Bloomfield         0.00           0.000000   
27                 Boerum Hill         0.00           0.000000   
28                Borough Park         0.00           0.000000   
29                Breezy Point         0.00           0.000000   
30                   Briarwood         0.00           0.000000   
31              Brighton Beach         0.00           0.000000   
32               Broad Channel         0.00           0.010101   
33           Broadway Junction         0.00           0.000000   
34                   Bronxdale         0.04           0.000000   
35            Brooklyn Heights         0.00           0.000000   
36                  Brookville         0.00           0.000000   
37                 Brownsville         0.00           0.000000   
38                  Bulls Head         0.00           0.000000   
39                    Bushwick         0.00           0.000000   
40                Butler Manor         0.00           0.000000   
41             Cambria Heights         0.00           0.000000   
42                    Canarsie         0.00           0.000000   
43               Carnegie Hill         0.00           0.000000   
44             Carroll Gardens         0.00           0.000000   
45                 Castle Hill         0.02           0.000000   
46           Castleton Corners         0.00           0.000000   
47              Central Harlem         0.00           0.000000   
48                  Charleston         0.00           0.000000   
49                     Chelsea         0.00           0.000000   
50                   Chinatown         0.00           0.000000   
51                 City Island         0.00           0.000000   
52                   City Line         0.00           0.000000   
53                Civic Center         0.00           0.000000   
54           Claremont Village         0.03           0.000000   
55                Clason Point         0.00           0.000000   
56                     Clifton         0.00           0.000000   
57                     Clinton         0.00           0.000000   
58                Clinton Hill         0.00           0.000000   
59                  Co-op City         0.00           0.00

#### Let's confirm the new size

In [30]:
newyork_grouped.shape

(302, 347)

#### Let's print each neighborhood along with the top 5 most common venues

In [31]:
num_top_venues = 5

for hood in newyork_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = newyork_grouped[newyork_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                venue  freq
0         Pizza Place  0.14
1  Italian Restaurant  0.09
2                 Zoo  0.07
3              Garden  0.06
4              Bakery  0.05


----Annadale----
                    venue  freq
0             Pizza Place  0.09
1      Italian Restaurant  0.06
2          Ice Cream Shop  0.05
3                    Park  0.04
4  Furniture / Home Store  0.04


----Arden Heights----
                venue  freq
0         Pizza Place  0.09
1  Italian Restaurant  0.07
2      Ice Cream Shop  0.05
3              Bakery  0.05
4                Park  0.04


----Arlington----
                venue  freq
0      Clothing Store  0.09
1  Italian Restaurant  0.06
2         Pizza Place  0.05
3              Bakery  0.05
4      Ice Cream Shop  0.05


----Arrochar----
                venue  freq
0  Italian Restaurant  0.14
1         Pizza Place  0.12
2                Park  0.05
3                 Bar  0.04
4               Beach  0.04


----Arverne----
         venue  fre

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [32]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [33]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = newyork_grouped['Neighborhood']

for ind in np.arange(newyork_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(newyork_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place    Italian Restaurant   
1       Annadale           Pizza Place    Italian Restaurant   
2  Arden Heights           Pizza Place    Italian Restaurant   
3      Arlington        Clothing Store    Italian Restaurant   
4       Arrochar    Italian Restaurant           Pizza Place   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                   Zoo                Garden                Bakery   
1        Ice Cream Shop                 Diner                Bakery   
2                Bakery        Ice Cream Shop                  Park   
3           Pizza Place        Ice Cream Shop                Bakery   
4                  Park                 Beach                   Bar   

  6th Most Common Venue   7th Most Common Venue 8th Most Common Venue  \
0         Deli / Bodega      Mexican Restaurant  Caribbean Restaurant   
1                  Park  Furniture / Home Store           Golf Course   
2        Clothing Store  Furniture / Home Store           Golf Course   
3      Department Store                     Bar            Bagel Shop   
4                Bakery                     Spa   Japanese Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0           Coffee Shop   Gym / Fitness Center  
1      Sushi Restaurant         Clothing Store  
2            Restaurant            Coffee Shop  
3   American Restaurant            Coffee Shop  
4         Deli / Bodega         Sandwich Place

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [34]:
# set number of clusters
kclusters = 5

newyork_grouped_clustering = newyork_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(newyork_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 4, 4, 4, 1, 2, 3, 3, 4, 4], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [35]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

newyork_merged = neighborhoods

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
newyork_merged = newyork_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

newyork_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201               4   
1   Bronx   Co-op City  40.874294 -73.829939               4   
2   Bronx  Eastchester  40.887556 -73.827806               4   
3   Bronx    Fieldston  40.895437 -73.905643               4   
4   Bronx    Riverdale  40.890834 -73.912585               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0           Pizza Place  Caribbean Restaurant                Bakery   
1           Pizza Place  Caribbean Restaurant    Italian Restaurant   
2           Pizza Place  Caribbean Restaurant                Bakery   
3           Pizza Place                  Park                Bakery   
4           Pizza Place                  Park                 Diner   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Burger Joint              Pharmacy                  Park   
1                Bakery    Seafood Restaurant    Mexican Restaurant   
2    Italian Restaurant              Pharmacy                  Park   
3    Mexican Restaurant                 Trail                 Diner   
4    Mexican Restaurant                  Café                 Trail   

  7th Most Common Venue      8th Most Common Venue 9th Most Common Venue  \
0    Seafood Restaurant       Fast Food Restaurant    Italian Restaurant   
1                 Diner                       Park  Fast Food Restaurant   
2    Mexican Restaurant       Fast Food Restaurant                   Gym   
3                   Bar               Burger Joint         Deli / Bodega   
4                Bakery  Latin American Restaurant                   Bar   

  10th Most Common Venue  
0         Ice Cream Shop  
1               Pharmacy  
2     Seafood Restaurant  
3         Scenic Lookout  
4           Burger Joint

Finally, let's visualize the resulting clusters

In [36]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(newyork_merged['Latitude'], newyork_merged['Longitude'], newyork_merged['Neighborhood'], newyork_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 5. Examine Clusters

#### Cluster 1

In [37]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 0, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
64      Brooklyn Heights                  Park    Italian Restaurant   
100            Chinatown                  Park             Bookstore   
106          East Harlem                  Park               Exhibit   
107      Upper East Side                  Park                   Gym   
108            Yorkville            Art Museum                  Park   
109           Lenox Hill               Theater                  Park   
110     Roosevelt Island                  Park                   Gym   
111      Upper West Side                  Park                Bakery   
112       Lincoln Square               Theater                   Gym   
113              Clinton               Theater                   Gym   
114              Midtown               Theater                   Gym   
115          Murray Hill     Korean Restaurant               Theater   
116              Chelsea                  Park               Theater   
117    Greenwich Village                  Park          Cycle Studio   
118         East Village                  Park                   Gym   
119      Lower East Side                  Park           Yoga Studio   
120              Tribeca                  Park             Bookstore   
121         Little Italy                  Park           Yoga Studio   
122                 Soho                  Park    Italian Restaurant   
123         West Village                  Park          Cycle Studio   
124     Manhattan Valley                  Park               Exhibit   
125  Morningside Heights                  Park               Exhibit   
126             Gramercy                  Park                   Gym   
127    Battery Park City                  Park    Italian Restaurant   
128   Financial District                  Park        Scenic Lookout   
139     Long Island City                  Park                   Gym   
180          Murray Hill     Korean Restaurant               Theater   
186           Ravenswood                  Park            Art Museum   
244              Chelsea                  Park               Theater   
247        Carnegie Hill                  Park                Bakery   
248                 Noho                  Park           Yoga Studio   
249         Civic Center                  Park    Italian Restaurant   
250        Midtown South               Theater                   Gym   
271         Sutton Place               Theater                   Gym   
272        Hunters Point                   Gym                  Park   
273           Turtle Bay               Theater                   Gym   
274           Tudor City               Theater                   Gym   
275      Stuyvesant Town                  Park                   Gym   
276             Flatiron                  Park               Theater   
279         Fulton Ferry                  Park    Italian Restaurant   
280         Vinegar Hill                  Park    Italian Restaurant   
283                Dumbo                  Park    Italian Restaurant   
301         Hudson Yards               Theater                   Gym   
304         Queensbridge                  Park                   Gym   

    3rd Most Common Venue     4th Most Common Venue 5th Most Common Venue  \
64            Coffee Shop             Memorial Site          Gourmet Shop   
100           Cheese Shop        Italian Restaurant           Salad Place   
106            Art Museum                    Bakery             Wine Shop   
107          Concert Hall                Art Museum                Bakery   
108                Bakery                       Gym               Exhibit   
109                   Gym              Concert Hall            Art Museum   
110               Theater                Art Museum          Concert Hall   
111          Concert Hall                   Theater            Art Museum   
112          Concert Hall                      Park                 Plaza   
1

#### Cluster 2

In [38]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 1, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
8                Norwood           Pizza Place                Garden   
9         Williamsbridge           Pizza Place                Bakery   
11        Pelham Parkway           Pizza Place                   Zoo   
12           City Island    Seafood Restaurant           Pizza Place   
13          Bedford Park           Pizza Place    Italian Restaurant   
14    University Heights           Pizza Place    Italian Restaurant   
15        Morris Heights                  Park    Italian Restaurant   
16               Fordham    Italian Restaurant           Pizza Place   
17          East Tremont    Italian Restaurant           Pizza Place   
18            West Farms    Italian Restaurant                   Zoo   
26             Soundview           Pizza Place    Mexican Restaurant   
27          Clason Point           Pizza Place                  Park   
28           Throgs Neck           Pizza Place                  Park   
29          Country Club           Pizza Place    Italian Restaurant   
30           Parkchester           Pizza Place                   Zoo   
31    Westchester Square           Pizza Place   American Restaurant   
32              Van Nest    Italian Restaurant           Pizza Place   
33           Morris Park           Pizza Place                   Zoo   
34               Belmont    Italian Restaurant           Pizza Place   
37            Pelham Bay           Pizza Place    Mexican Restaurant   
38         Schuylerville           Pizza Place    Italian Restaurant   
39        Edgewater Park           Pizza Place    Italian Restaurant   
40           Castle Hill           Pizza Place                  Park   
41             Olinville           Pizza Place    Italian Restaurant   
42        Pelham Gardens           Pizza Place    Italian Restaurant   
44             Unionport           Pizza Place                   Zoo   
47           Bensonhurst           Pizza Place    Italian Restaurant   
140            Sunnyside    Italian Restaurant           Pizza Place   
197           St. George    Italian Restaurant           Pizza Place   
198         New Brighton    Italian Restaurant                   Bar   
199            Stapleton    Italian Restaurant           Pizza Place   
200             Rosebank    Italian Restaurant           Pizza Place   
201        West Brighton           Pizza Place    Italian Restaurant   
202          Grymes Hill    Italian Restaurant           Pizza Place   
203            Todt Hill    Italian Restaurant           Pizza Place   
204          South Beach    Italian Restaurant           Pizza Place   
205        Port Richmond           Pizza Place                   Bar   
208    Castleton Corners           Pizza Place    Italian Restaurant   
211             New Dorp    Italian Restaurant           Pizza Place   
212              Oakwood    Italian Restaurant           Pizza Place   
213          Great Kills    Italian Restaurant           Pizza Place   
218        Tompkinsville    Italian Restaurant           Pizza Place   
219          Silver Lake    Italian Restaurant           Pizza Place   
220            Sunnyside    Italian Restaurant           Pizza Place   
224            Park Hill    Italian Restaurant           Pizza Place   
225          Westerleigh    Italian Restaurant           Pizza Place   
228             Arrochar    Italian Restaurant           Pizza Place   
229             Grasmere    Italian Restaurant           Pizza Place   
230             Old Town    Italian Restaurant           Pizza Place   
231         Dongan Hills    Italian Restaurant           Pizza Place   
232        Midland Beach    Italian Restaurant           Pizza Place   
233           Grant City    Italian Restaurant           Pizza Place   
234       New Dorp Beach    Italian Restaurant           Pizza Place   
251        Richmond Town    Italian Restaurant           Pizza Place   
252          Shore Acres    Italian Restaurant      

#### Cluster 3

In [39]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 2, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
170    Far Rockaway                 Beach           Coffee Shop   
171   Broad Channel                 Beach             Surf Spot   
176        Edgemere                 Beach            Bagel Shop   
177         Arverne                 Beach            Bagel Shop   
178  Rockaway Beach                 Beach            Bagel Shop   
179        Neponsit                 Beach                   Bar   
190    Belle Harbor                 Beach            Bagel Shop   
191   Rockaway Park                 Beach             Surf Spot   
192      Somerville                 Beach           Pizza Place   
288         Roxbury                 Beach            Donut Shop   
302         Hammels                 Beach             Surf Spot   
303       Bayswater                 Beach        Airport Lounge   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
170           Golf Course            Bagel Shop           Pizza Place   
171            Bagel Shop            Donut Shop           Pizza Place   
176           Pizza Place             Surf Spot                   Bar   
177             Surf Spot                   Bar           Pizza Place   
178             Surf Spot           Pizza Place            Donut Shop   
179            Bagel Shop             Beach Bar           Pizza Place   
190                   Bar             Surf Spot             Beach Bar   
191            Bagel Shop                   Bar         National Park   
192            Donut Shop             Surf Spot            Bagel Shop   
288            Bagel Shop                  Bank    Turkish Restaurant   
302            Bagel Shop           Pizza Place                   Bar   
303           Coffee Shop           Pizza Place             Surf Spot   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
170             Surf Spot        Sandwich Place    Italian Restaurant   
171                   Bar             Beach Bar              Wine Bar   
176    Chinese Restaurant           Coffee Shop          Burger Joint   
177    Italian Restaurant             Beach Bar    Chinese Restaurant   
178                   Bar         Deli / Bodega                  Park   
179            Restaurant           Golf Course               Theater   
190           Pizza Place            Restaurant                Bakery   
191                  Park                Bakery             Beach Bar   
192                   Bar        Sandwich Place           Coffee Shop   
288            Restaurant           Pizza Place              Pharmacy   
302              Wine Bar              Pharmacy                Bakery   
303           Golf Course            Bagel Shop    Chinese Restaurant   

    9th Most Common Venue 10th Most Common Venue  
170           Supermarket         Airport Lounge  
171         Deli / Bodega               Boutique  
176                Bakery     Italian Restaurant  
177                Bakery               Pharmacy  
178            Restaurant            Coffee Shop  
179                Bakery        Harbor / Marina  
190         National Park     Seafood Restaurant  
191           Coffee Shop            Pizza Place  
192    Chinese Restaurant           Burger Joint  
288                  Park         Ice Cream Shop  
302             Beach Bar            Coffee Shop  
303          Burger Joint                 Bakery

#### Cluster 4

In [40]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 3, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
19                High  Bridge                  Park             Wine Shop   
20                     Melrose                  Park           Coffee Shop   
21                  Mott Haven                  Park                   Bar   
22                 Port Morris                  Park           Pizza Place   
23                    Longwood                Bakery           Pizza Place   
24                 Hunts Point                  Park    Mexican Restaurant   
25                  Morrisania    Italian Restaurant                   Zoo   
35              Spuyten Duyvil           Pizza Place    Mexican Restaurant   
43                   Concourse    Italian Restaurant    Mexican Restaurant   
48                 Sunset Park                  Park                   Bar   
49                  Greenpoint           Pizza Place                  Park   
54                    Flatbush  Caribbean Restaurant                  Café   
55               Crown Heights                   Bar           Pizza Place   
56               East Flatbush  Caribbean Restaurant                  Café   
57                  Kensington                   Bar                  Park   
58             Windsor Terrace                  Park                   Bar   
59            Prospect Heights           Pizza Place          Cocktail Bar   
60                 Brownsville                   Bar           Pizza Place   
61                Williamsburg           Pizza Place                  Park   
62                    Bushwick           Pizza Place                   Bar   
63          Bedford Stuyvesant           Pizza Place                   Bar   
65                 Cobble Hill                  Park           Coffee Shop   
66             Carroll Gardens                  Park        Ice Cream Shop   
67                    Red Hook                  Park           Coffee Shop   
68                     Gowanus           Coffee Shop                   Bar   
69                 Fort Greene                  Park           Pizza Place   
70                  Park Slope           Pizza Place           Coffee Shop   
71               Cypress Hills           Pizza Place                   Bar   
72               East New York           Pizza Place                Bakery   
80                Borough Park           Pizza Place                  Park   
84                Clinton Hill                  Park           Pizza Place   
86                    Downtown           Pizza Place                  Park   
87                 Boerum Hill                  Park           Pizza Place   
88   Prospect Lefferts Gardens                   Bar          Cocktail Bar   
89                  Ocean Hill                   Bar           Pizza Place   
93         Prospect Park South                   Bar                  Park   
95           East Williamsburg           Pizza Place                   Bar   
96                  North Side                  Park           Pizza Place   
97                  South Side                  Park           Pizza Place   
101         Washington Heights                  Park                  Café   
102                     Inwood           Pizza Place                  Park   
103           Hamilton Heights                  Park           Coffee Shop   
104             Manhattanville                  Park    Italian Restaurant   
105             Central Harlem                  Park           Pizza Place   
129                    Astoria           Pizza Place                   Bar   
130                   Woodside           Pizza Place       Thai Restaurant   
142                    Maspeth           Pizza Place                   Bar   
143                  Ridgewood                   Bar           Pizza Place   
144                   Glendale           Pizza Place                   Bar   
173                   Steinway                   Bar            Bagel Shop   
221                Ditmas Park          